In [1]:
import numpy as np
import pandas as pd
import folium
import webbrowser
import os
import math

from h3 import h3
from folium import Map

In [2]:
all_wards = pd.read_csv('~/Downloads/Wards_Boundaries_in_the_UK_.csv')
all_wards.dropna()

objectid     wd17cd        ward_name   bng_e   bng_n       lng  \
0            1  E05000026            Abbey  544434  184378  0.081291   
1            2  E05000027           Alibon  549247  185196  0.150987   
2            3  E05000028        Becontree  546863  185869  0.116912   
3            4  E05000029   Chadwell Heath  548266  189340  0.138596   
4            5  E05000030        Eastbrook  550774  186272  0.173453   
...        ...        ...              ...     ...     ...       ...   
9126      9127  W05001034    Seven Sisters  282205  208034 -3.708120   
9127      9128  W05001035         Tai-bach  278526  188941 -3.754750   
9128      9129  W05001036  Broughton South  333635  362976 -2.994000   
9129      9130  W05001037          Penally  211555  200954 -4.726920   
9130      9131  W05001038     Tenby: North  212785  201537 -4.709460   

            lat  st_areashape  st_lengthshape  
0     51.539822      0.000163        0.095056  
1     51.545921      0.000177        0.081044  
2     51.552601      0.000167        0.075036  
3     51.583420      0.000439        0.108753  
4     51.555191      0.000447        0.106966  
...         ...           ...             ...  
9126  51.758572      0.001516        0.190597  
9127  51.586189      0.000718        0.156890  
9128  53.159771      0.000429        0.156155  
9129  51.675659      0.002761        0.378792  
9130  51.681309      0.000210        0.080948  

[9131 rows x 9 columns]

In [3]:
def create_map(clusters):
    # Create the map object
    map = Map(tiles="cartodbpositron")
    
    # map = Map(tiles="cartodbdark_matter")              #alternative map type
    # map = Map(tiles="openstreetmap")                   #alternative map type

    # Convert the clusters dictionary items to polygons and add them to the map
    for cluster in clusters.values():
        points = cluster['geom']
        # points = [p[::-1] for p in points]
        if cluster['count'] ==1:
            tooltip = "{0} ward".format(cluster['count'])     # when hover an area, displays number of constituencies
        else:
            tooltip = "{0} wards".format(cluster['count'])     # when hover an area, displays number of constituencies

        polygon = folium.vector_layers.Polygon(locations=points, tooltip=tooltip,
                                               fill=True, 
                                               color='#ff0000', 
                                               fill_color='#ff0000', 
                                               fill_opacity=0.4, weight=3, opacity=0.4)
        polygon.add_to(map)

    # Determine the map bounding box
    max_lat = df.lat.max()
    min_lat = df.lat.min()
    max_lon = df.lng.max()
    min_lon = df.lng.min()
    
    # Fit the map to the bounds
    map.fit_bounds([[min_lat, min_lon], [max_lat, max_lon]])
    
    return map

In [4]:
h3_level = 7           # best values to use: 4,5,6,7

In [5]:
# iterates through each number in the individual conlumns of the dataset and converts them to an h3 index
def lat_lng_to_h3(row):
    return h3.geo_to_h3(row['lat'], row['lng'], h3_level)

In [6]:
# adds new column with h3 index to dataset
all_wards['h3_index_rep'] = all_wards.apply(lat_lng_to_h3, axis=1)

In [7]:
df = all_wards.copy()
df.head(n=651)

objectid     wd17cd        ward_name   bng_e   bng_n       lng  \
0           1  E05000026            Abbey  544434  184378  0.081291   
1           2  E05000027           Alibon  549247  185196  0.150987   
2           3  E05000028        Becontree  546863  185869  0.116912   
3           4  E05000029   Chadwell Heath  548266  189340  0.138596   
4           5  E05000030        Eastbrook  550774  186272  0.173453   
..        ...        ...              ...     ...     ...       ...   
646       647  E05000726  Failsworth West  389265  401051 -2.163320   
647       648  E05000727       Hollinwood  391741  402481 -2.126020   
648       649  E05000728     Medlock Vale  393316  402612 -2.102270   
649       650  E05000729     Royton North  390935  408176 -2.138350   
650       651  E05000730     Royton South  392425  407457 -2.115830   

           lat  st_areashape  st_lengthshape     h3_index_rep  
0    51.539822      0.000163        0.095056  87194e68dffffff  
1    51.545921      0.000177        0.081044  87194e6f4ffffff  
2    51.552601      0.000167        0.075036  87194e6abffffff  
3    51.583420      0.000439        0.108753  87194e6adffffff  
4    51.555191      0.000447        0.106966  87194e61affffff  
..         ...           ...             ...              ...  
646  53.506050      0.000347        0.123521  8719424caffffff  
647  53.518951      0.000376        0.108779  8719424ceffffff  
648  53.520149      0.000492        0.148809  8719424ccffffff  
649  53.570122      0.000683        0.127389  8719424c4ffffff  
650  53.563679      0.000545        0.152545  8719424c5ffffff  

[651 rows x 10 columns]

In [8]:
h3_clusters = dict()

for index, row in all_wards.iterrows():
    key = row['h3_index_rep']
    if key in h3_clusters:
        h3_clusters[key]["count"] += 1
    else:
        h3_clusters[key] = {"count": 1,
                            "geom": h3.h3_to_geo_boundary(key)}

In [9]:
relevant_clusters = { key:value for (key,value) in h3_clusters.items() if value['count'] >= 0}

In [10]:
h3_map = create_map(relevant_clusters)

In [11]:
h3_map